# MSC Plugin

In [1]:
import set_env
from pathlib import Path

temp_dir = Path(".temp")
temp_dir.mkdir(exist_ok=True)

参考：[【我与TVM二三事 后篇（5）】MSC之PluginBuilder](https://zhuanlan.zhihu.com/p/681450076)

In [2]:
from utils import *
from utils import _build_plugin

In [3]:
frameworks = [MSCFramework.TORCH, MSCFramework.TVM]
if tvm.get_global_func("relax.ext.tensorrt", True) is not None:
    frameworks.append(MSCFramework.TENSORRT)
plugin_root = msc_utils.msc_dir(f"{temp_dir}/msc_plugin")
managers = _build_plugin(frameworks, plugin_root)

# test the plugin load
_test_tvm_plugin(managers[MSCFramework.TVM], "llvm")
if tvm.cuda().exist:
    _test_tvm_plugin(managers[MSCFramework.TVM], "cuda")
_test_torch_plugin(managers[MSCFramework.TORCH])

# test the plugin with manager
model_info = {
    "inputs": [
        {"name": "input_0", "shape": [1, 3, 224, 224], "dtype": "float32", "layout": "NCHW"}
    ],
    "outputs": [
        {"name": "output", "shape": [1, 6, 218, 218], "dtype": "float32", "layout": "NCHW"}
    ],
    "nodes": {"total": 4, "input": 1, "msc.conv2d_bias": 1, "MyRelu": 1, "nn.max_pool2d": 1},
}
_test_with_manager(managers, MSCFramework.TORCH, model_info, temp_dir)
_test_with_manager(managers, MSCFramework.TVM, model_info, temp_dir)
if tvm.get_global_func("relax.ext.tensorrt", True) is not None:
    byoc_info = {
        "inputs": [
            {"name": "input_0", "shape": [1, 3, 224, 224], "dtype": "float32", "layout": "NCHW"}
        ],
        "outputs": [
            {"name": "output", "shape": [1, 6, 218, 218], "dtype": "float32", "layout": ""}
        ],
        "nodes": {"total": 2, "input": 1, "msc_tensorrt": 1},
    }
    _test_with_manager(managers, MSCFramework.TENSORRT, byoc_info, temp_dir)

plugin_root.destory()


AssertionError: Failed to build plugin under /media/pc/data/lxw/ai/tvm-book/doc/tutorials/msc/plugin/.temp/msc_plugin/install/source_torch/build, check codegen.log for detail